# 模型数据相关 API

在 Masmod 中，我们使用 `polars.DataFrame` 类的对象作为模型数据用于数据检视，模型拟合与模拟等场景。对于 `polars.DataFrame` 的入门以及使用技巧可参考 [Python 数据科学入门](../pre/python-data-science.ipynb)。

在群体建模场景下，我们使用与 `NONMEM` 互相兼容的数据列映射，如 `ID`, `TIME`, `DV` 等。此外，我们也可以通过 `EventTable()` 工具来快速构建符合不同场景的模拟数据集用于模型模拟。


In [1]:
from mas.datasets import warfarin
import polars as pl

## 数据检视

(plot-profile)=

### plot_profile()

```{py:method} plot_profile(data, scatter=True, line=True, idv_name=None, dv_name=None, **style) -> Plot

```

绘制因变量与自变量的折线图。

**参数：**

- **data** _(`DataFrame`)_：数据集。
- **scatter** _(`bool`, optional)_：是否在图形中绘制散点。默认值为 `True`。
- **line** _(`bool`, optional)_：是否在图形中绘制折线。默认值为 `True`。
- **idv_name** _(`str`, optional)_：因变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dv_name** _(`str`, optional)_：自变量名。若为 `None`，则自动推断。默认值为 `None`。
- **\*\*style**: 样式相关设置

**返回值：**

绘制完成的因变量与自变量折线图。

**返回类型：**

`Plot`


In [2]:
from mas.model import plot_profile

plot_profile(warfarin.filter(pl.col("DVID") == 1)).with_facet_wrap("SEX")

(plot-covariates)=

### plot_covariates()

```{py:method} plot_covariates(data, *, categorical=None, include=None, **style) -> GridPlot

```

```{py:method} plot_covariates(data, *, categorical=None, exclude=None, **style) -> GridPlot

```

绘制协变量矩阵图。

**参数：**

- **data** _(`DataFrame`)_：数据集。
- **categorical** _(`list[str]`, optional)_：需要作为分类变量的列名。若为 `None`，则自动推断。默认值为 `None`。
- **include** _(`list[str]`, optional)_：需要纳入的协变量。若为 `None`，则纳入所有列。默认值为 `None`。
- **exclude** _(`list[str]`, optional)_：需要剔除的协变量。若为 `None`，则无剔除列。默认值为 `None`。
- **\*\*style**: 样式相关设置

**返回值：**

绘制完成的协变量矩阵图。

**返回类型：**

`GridPlot`


In [3]:
from mas.model import plot_covariates

plot_covariates(warfarin, categorical=["SEX"], exclude=["DVID"]).with_layout(width=600, height=600)

(plot-bivariate)=

### plot_bivariate()

```{py:method} plot_bivariate(data, dvid_name="DVID", idv_name=None, dv_name=None, dvid_x=1, dvid_y=2, **style) -> Plot

```

绘制两类因变量的关系折线图。

**参数：**

- **data** _(`DataFrame`)_：数据集。
- **dvid_name** _(`str`, optional)_：作为 `DVID` 使用的列名，默认为 `"DVID"`。
- **idv_name** _(`str`, optional)_：因变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dv_name** _(`str`, optional)_：自变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dvid_x** _(`str | int | float`, optional)_：作为 `x` 使用的 `DVID` 值，默认为 `1`。
- **dvid_y** _(`str | int | float`, optional)_：作为 `y` 使用的 `DVID` 值，默认为 `2`。
- **\*\*style**: 样式相关设置

**返回值：**

绘制完成的两类因变量的关系折线图。

**返回类型：**

`Plot`


In [4]:
from mas.model import plot_bivariate

plot_bivariate(warfarin, dvid_x=1, dvid_y=2).with_title(text="两变量关系图")

## NONMEM 数据录入

(read-nonmem-data)=

### read_nonmem_data()

```{py:method} read_nonmem_data(path, ignore="#", encoding="utf-8", columns=None) -> DataFrame

```

读取本地 NONMEM 数据文件为 DataFrame

**参数：**

- **path** _(`PathLike`)_：NONMEM 数据文件的路径。
- **ignore** _(`str`, optional)_：忽略以 `ignore` 开头的行。与 NONMEM 控制文件中 `$DATA` 的 `IGNORE` 功能一致。默认为 `"#"`。
- **encoding** _(`str`, optional)_：数据文件编码。默认值为 `"utf-8"`
- **columns** _(`list[str | NonmemDrop]`, optional)_：数据集列名。与 NONMEM 控制文件中 `$INPUT` 功能一致。若为 `None`，则将使用 `Unnamed_i` 作为列名，`i` 为列的索引序号。默认值为 `None`。

**返回值：**

读取自 NONMEM 数据集的 `DataFrame` 数据框。

**返回类型：**

`DataFrame`


(EventTable)=

## EventTable

`EventTable` 是一个非常实用的工具类，它能够帮助我们快速的构建出可以用于模型模拟或者拟合的标准格式的数据集。通过 `EventTable` 你可以对一个现有数据添加一系列新的观测点，也可以模拟不同给药场景。又或者我们可以通过 `EventTable` 从零开始创建一个全新的数据集。


```{py:class} EventTable(data=None, schema=None)

```

构造 `EventTable` 对象

**参数：**

- **data** _(`FrameInitTypes`, optional)_：起始数据集。如果为 `None` 则从空数据开始构建。默认值为 `None`。
- **schema** _(`SchemaDefinition`, optional)_：数据集的列名以及列类型定义。如果为 `None` 则自动推断。默认值为 `None`。

:::{tip}
`data` 和 `schema` 参数的使用方法可以另见：[polars.DataFrame](https://docs.pola.rs/api/python/stable/reference/dataframe/index.html)。
:::


(EventTable-doses)=

### doses

```{py:property} doses

```

获取数据中的给药数据。

**类型：**

`DataFrame`

(EventTable-observations)=

### observations

```{py:property} observations

```

获取数据中的观测数据。

**类型：**

`DataFrame`


### add_dosing()

```{py:method} add_dosing(self, time, amt, id=None, cmt=None, addl=None, ii=None, dur=None, rate=None, ss=None) -> Self

```

向 `EventTable` 中添加给药记录。

**参数：**

- **time** _(`Numeric` | Numeric)_：给药时间。
- **amt** _(`Numeric` | Numeric)_：给药剂量。
- **id** _(`IdLike`, optional)_：需要增加给药记录的受试者编号。若为 `None`，则为所有受试者增加给药记录。默认值为 `None`。
- **addl** _(`Int`, optional)_：额外给药次数。默认值为 `None`。
- **ii** _(`Numeric`, optional)_：给药间隔。默认值为 `None`。
- **cmt** _(`Int`, optional)_：给药房室编号。默认值为 `None`。
- **rate** _(`Numeric`, optional)_：给药速率。若为正数，将视为滴注速率；若为 `0`，将视为推注给药；若为 `-1`，则意为将对给药速率建模；若为 `-2`，则意为将对给药持续时间建模。不能与 `dur` 同时设置。默认值为 `None`。
- **dur** _(`Numeric`, optional)_：给药持续时间。不能与 `rate` 同时设置。默认值为 `None`。
- **ss** _(`Numeric`, optional)_：稳态标记。默认值为 `None`。

**返回值：**

更新后的 `EventTable`

**返回类型：**

`EventTable`


### add_sampling()

```{py:method} add_dosing(self, time, id=None) -> Self

```

向 `EventTable` 中添加观测记录。

**参数：**

- **time** _(`VectorLike | Numeric`)_：观测时间。
- **id** _(`IdLike`, optional)_：需要增加观测记录的受试者编号。若为 `None`，则为所有受试者增加观测记录。默认值为 `None`。

**返回值：**

更新后的 `EventTable`

**返回类型：**

`EventTable`


### with_covariates()

```{py:method} with_covariates(self, *, id=None, **kwargs) -> Self

```

为 `EventTable` 添加协变量。

如果不提供 `id`，则协变量只能填写单一值，该值会应用到当前数据集中的每一行上。如果提供 `id`，则会根据 `id` 设置协变量。

**参数：**

- **id** _(`Int`, optional)_：需要添加协变量的受试者编号。若为 `None`，则为所有受试者添加协变量。默认值为 `None`。
- **\*\*kwargs**: 协变量，如 `WT=60`

**返回值：**

更新后的 `EventTable`

**返回类型：**

`EventTable`


### with_ids()

```{py:method} with_ids(self, *, ids, reset_id=False) -> Self

```

为 `EventTable` 根据提供的 `id` 执行扩展。

**参数：**

- **ids** _(`Iterable[Int]`)_：需要扩展的 `id`。
- **reset_id** _(`bool`, optional)_: 如果当前 `EventTable` 存在 `id` 是否需要重置。默认值为 `False`

**返回值：**

更新后的 `EventTable`

**返回类型：**

`EventTable`
